<a href="https://colab.research.google.com/github/IceCream0910/taein-tts/blob/main/voice_cloning_using_xtts.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Voice Cloning with Zero-Shot Multi-Speaker model XTTS-v2

## Installing dependencies

In [1]:
import locale
locale.getpreferredencoding = lambda: "UTF-8"

In [2]:
!sudo apt install portaudio19-dev

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
The following additional packages will be installed:
  libportaudio2 libportaudiocpp0
Suggested packages:
  portaudio19-doc
The following NEW packages will be installed:
  libportaudio2 libportaudiocpp0 portaudio19-dev
0 upgraded, 3 newly installed, 0 to remove and 49 not upgraded.
Need to get 188 kB of archives.
After this operation, 927 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy/universe amd64 libportaudio2 amd64 19.6.0-1.1 [65.3 kB]
Get:2 http://archive.ubuntu.com/ubuntu jammy/universe amd64 libportaudiocpp0 amd64 19.6.0-1.1 [16.1 kB]
Get:3 http://archive.ubuntu.com/ubuntu jammy/universe amd64 portaudio19-dev amd64 19.6.0-1.1 [106 kB]
Fetched 188 kB in 1s (163 kB/s)
debconf: unable to initialize frontend: Dialog
debconf: (No usable dialog-like program is installed, so the dialog based frontend cannot be used. at /usr/share/perl5/Debconf/FrontEn

In [3]:
pip install --quiet TTS scipy sounddevice wavio PyAudio ffmpeg-python pydub

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 47.1/47.1 kB 4.0 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.5/73.5 kB 7.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 66.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.6/101.6 kB 7.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.3/15.3 MB 104.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 31.4/31.4 MB 27.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.1/18.1 MB 72.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━

In [29]:
!pip install pydub scipy

## Cloning the Repository

In [4]:
!git clone https://huggingface.co/coqui/XTTS-v2

Cloning into 'XTTS-v2'...
remote: Enumerating objects: 161, done.
remote: Counting objects: 100% (157/157), done.
remote: Compressing objects: 100% (151/151), done.
remote: Total 161 (delta 69), reused 0 (delta 0), pack-reused 4 (from 1)
Receiving objects: 100% (161/161), 2.29 MiB | 10.54 MiB/s, done.
Resolving deltas: 100% (69/69), done.
Filtering content: 100% (4/4), 1.94 GiB | 31.45 MiB/s, done.


## Import Libraries

In [5]:
from TTS.tts.configs.xtts_config import XttsConfig
from TTS.tts.models.xtts import Xtts

from IPython.display import Audio
from scipy.io.wavfile import write
import matplotlib.pyplot as plt

import sounddevice as sd
from scipy.io.wavfile import write
import wavio as wv

import os
import scipy.io.wavfile as wavfile

## Record your own custom voice

In [6]:
sampling_freq = 44100
duration = 5

In [9]:
from IPython.display import HTML, Audio
from google.colab.output import eval_js
from base64 import b64decode
import numpy as np
from scipy.io.wavfile import read as wav_read
import io
import ffmpeg

AUDIO_HTML = """
<script>
var my_div = document.createElement("DIV");
var my_p = document.createElement("P");
var my_btn = document.createElement("BUTTON");
var t = document.createTextNode("Press to start recording");

my_btn.appendChild(t);
my_div.appendChild(my_btn);
document.body.appendChild(my_div);

var base64data = 0;
var reader;
var recorder, gumStream;
var recordButton = my_btn;

var handleSuccess = function(stream) {
  gumStream = stream;
  var options = {
    mimeType : 'audio/webm;codecs=opus'
  };
  recorder = new MediaRecorder(stream);
  recorder.ondataavailable = function(e) {
    var url = URL.createObjectURL(e.data);
    var preview = document.createElement('audio');
    preview.controls = true;
    preview.src = url;
    document.body.appendChild(preview);

    reader = new FileReader();
    reader.readAsDataURL(e.data);
    reader.onloadend = function() {
      base64data = reader.result;
    }
  };
  recorder.start();
};

recordButton.innerText = "Recording... press to stop";

navigator.mediaDevices.getUserMedia({audio: true}).then(handleSuccess);

function toggleRecording() {
  if (recorder && recorder.state == "recording") {
      recorder.stop();
      gumStream.getAudioTracks()[0].stop();
      recordButton.innerText = "Saving the recording... pls wait!"
  }
}

function sleep(ms) {
  return new Promise(resolve => setTimeout(resolve, ms));
}

var data = new Promise(resolve=>{
recordButton.onclick = ()=>{
toggleRecording()
sleep(2000).then(() => {
  resolve(base64data.toString())
});
}
});

</script>
"""

def get_audio():
  display(HTML(AUDIO_HTML))
  data = eval_js("data")
  binary = b64decode(data.split(',')[1])

  # Convert the audio from webm to wav format using ffmpeg
  process = (ffmpeg
    .input('pipe:0')
    .output('pipe:1', format='wav')
    .run_async(pipe_stdin=True, pipe_stdout=True, pipe_stderr=True, quiet=True, overwrite_output=True)
  )
  output, err = process.communicate(input=binary)

  # Save the wav file
  with open('output_audio.wav', 'wb') as f:
    f.write(output)

  # Optionally, read the saved audio for further processing
  sr, audio = wav_read(io.BytesIO(output))

  return audio, sr


### Record audio

In [10]:
audio, sr = get_audio()

<ipython-input-9-a11643b8623f>:93: WavFileWarning: Reached EOF prematurely; finished at 362959 bytes, expected 4294967303 bytes from header.
  sr, audio = wav_read(io.BytesIO(output))


In [11]:
plt.figure(figsize=(20,10))
plt.plot(audio)
plt.show()

## Load the model for Inference

In [ ]:
#  모델 로딩
config = XttsConfig()
config.load_json("./XTTS-v2/config.json")
model = Xtts.init_from_config(config)
model.load_checkpoint(config, checkpoint_dir="./XTTS-v2/")
model.cuda()

In [44]:
import os
import re
from pydub import AudioSegment

# 텍스트를 한 문장 단위로 분리하는 함수
def split_text(text):
    sentences = re.split(r'(?<=\.)|(?<=\!)|(?<=\?)', text.strip())
    return [sentence.strip() for sentence in sentences if sentence.strip()]

# 합성할 긴 텍스트
text_to_speak = """
우주 여행이 보편화된 미래에, 한 노인 ‘안나’는 우주 정거장에 홀로 남아 남편과 아들이 있는 ‘슬렌포니아 제 3행성’으로 향하는 우주선이 오기를 기다린다. 그녀는 동면 기술인 ‘딥프리징’을 연구하여 유의미한 성과를 내고 있던 과학자였다. 그러나 동면 기술 없이도 우주를 여행할 수 있는 웜홀 항법이 개발되면서, 그녀의 연구는 빛을 잃는다. 더군다나 가족들이 있는 슬렌포니아에는 웜홀 통로가 발견되지 않았다는 이유로 우주선이 끊기게 되며, 가족들과의 이별을 맞이한다.
"""
reference_audios = ["./ref.wav"]

# 출력 폴더 생성 (없으면)
os.makedirs("outputs", exist_ok=True)

# 긴 텍스트를 문장 단위로 분리
sentences = split_text(text_to_speak)

# 각 문장에 대해 음성을 합성하고 개별 파일로 저장
for idx, sentence in enumerate(sentences):
    print(f"Processing sentence {idx + 1}/{len(sentences)}: {sentence}")
    output = model.synthesize(
        sentence,
        config,
        speaker_wav=reference_audios,
        gpt_cond_len=3,
        language="ko",
    )

    wav_data = output['wav']
    out_file_path = os.path.join("./outputs", f"output{idx + 1}.wav")
    wavfile.write(out_file_path, 24000, wav_data)


# ./outputs 폴더에 있는 wav 파일들을 output뒤에 있는 숫자 순서대로 병합하여 하나의 wav 파일로 생성
output_files = [f for f in os.listdir("./outputs") if f.startswith("output") and f.endswith(".wav")]
output_files.sort(key=lambda f: int(re.search(r"output(\d+)\.wav", f).group(1)))

# 0.5초 묵음 생성
silence = AudioSegment.silent(duration=500)

combined_audio = AudioSegment.empty()
for file in output_files:
    audio_segment = AudioSegment.from_wav(os.path.join("./outputs", file))
    combined_audio += audio_segment
    combined_audio += silence  # 각 audio segment 뒤에 묵음 추가

combined_audio.export("./outputs/combined_output.wav", format="wav")
print("Combined audio file created: ./outputs/combined_output.wav")


Processing sentence 1/4: 우주 여행이 보편화된 미래에, 한 노인 ‘안나’는 우주 정거장에 홀로 남아 남편과 아들이 있는 ‘슬렌포니아 제 3행성’으로 향하는 우주선이 오기를 기다린다.
Processing sentence 2/4: 그녀는 동면 기술인 ‘딥프리징’을 연구하여 유의미한 성과를 내고 있던 과학자였다.
Processing sentence 3/4: 그러나 동면 기술 없이도 우주를 여행할 수 있는 웜홀 항법이 개발되면서, 그녀의 연구는 빛을 잃는다.
Processing sentence 4/4: 더군다나 가족들이 있는 슬렌포니아에는 웜홀 통로가 발견되지 않았다는 이유로 우주선이 끊기게 되며, 가족들과의 이별을 맞이한다.
Combined audio file created: ./outputs/combined_output.wav


## for french language

In [14]:
config = XttsConfig()
config.load_json("./XTTS-v2/config.json")
model = Xtts.init_from_config(config)
model.load_checkpoint(config, checkpoint_dir="./XTTS-v2/")
model.cuda()

text_to_speak = "comment vas-tu"
reference_audios = ["./XTTS-v2/samples/fr_sample.wav"]

outputs_2 = model.synthesize(
    text_to_speak,
    config,
    speaker_wav=reference_audios,
    gpt_cond_len=3,
    language="fr",
)

## Audio Output

In [32]:
Audio(data=outputs_1['wav'], rate=24000)

In [45]:
# outputs 폴더 내의 모든 .wav 파일을 찾고 Audio 태그로 표시
output_folder = "outputs"
wav_files = [f for f in os.listdir(output_folder) if f.endswith(".wav")]

# 각 파일을 Audio 태그로 표시
for wav_file in wav_files:
    file_path = os.path.join(output_folder, wav_file)
    display(Audio(file_path))

### Save the Audio

In [17]:
out_dir = "./outputs"
out_file_path_1 = os.path.join(out_dir, "output1.wav")
out_file_path_2 = os.path.join(out_dir, "output2.wav")

# Create the output directory if it doesn't exist
if not os.path.exists(out_dir):
    os.makedirs(out_dir)

# Save the first wav (english) file
wavfile.write(out_file_path_1, 24000, outputs_1['wav'])

# Save the second (french) wav file
wavfile.write(out_file_path_2, 24000, outputs_2['wav'])
